In [1]:
import tifffile
from tqdm import tqdm
from pathlib import Path
from cellpose import models
import numpy as np
from skimage import measure, exposure, filters
import pandas as pd
import napari


In [2]:
# Scan for all images present in the data folder and add their Paths to the images list
data_path = Path("./data")
images = []

for file_path in data_path.glob("**/**/**/*.lsm"):
    images.append(file_path)

In [3]:
model = models.Cellpose(gpu=True, model_type="nuclei")
cellpose_nuclei_diameter = 40
gaussian_sigma = 2
dataframes = []

for image in tqdm(images):

    # Extract filename, region, mouse and IHC round
    file_path = Path(image)
    file_path_parts = file_path.parts
    filename = file_path.stem
    region = file_path_parts[-2]
    mouse_id = file_path_parts[-3]
    ihc_round = file_path_parts[-4]

    # Read the image file
    img = tifffile.imread(image)

    # Extract per channel info
    nuclei_img = img[0,:,:]
    h2a_img = img[1,:,:]
    cfos_img = img[2,:,:]

    # Create a copy of nuclei_mip
    input_img = nuclei_img.copy()

    # Might need to perform a Gaussian-blur before
    post_gaussian_img = filters.gaussian(
        input_img, sigma=gaussian_sigma
    )

    # Apply Contrast Stretching to improve Cellpose detection of overly bright nuclei
    p2, p98 = np.percentile(post_gaussian_img, (2, 98))
    img_rescale = exposure.rescale_intensity(
        post_gaussian_img, in_range=(p2, p98)
    )

    # Predict nuclei nuclei_masks using cellpose
    nuclei_masks, flows, styles, diams = model.eval(
        img_rescale,
        diameter=cellpose_nuclei_diameter,
        channels=[0, 0],
        net_avg=False,
                )
    
    # Extract regionprops from nuclei labels and H2A channel
    h2a_props = measure.regionprops_table(
        label_image=nuclei_masks,
        intensity_image=h2a_img,
        properties=[
            "label",
            "intensity_mean",
            "intensity_max",
            "area_filled",
            "perimeter",
            "equivalent_diameter"
        ],
    )

    # Construct a dataframe
    h2a_df = pd.DataFrame(h2a_props)

    # Rename the intensity columns for further merging with cfos_df
    h2a_df.rename(columns={'intensity_mean': 'h2a_intensity_mean'}, inplace=True)
    h2a_df.rename(columns={'intensity_max': 'h2a_intensity_max'}, inplace=True)
    
    # Extract regionprops from nuclei labels and CFOS channel
    cfos_props = measure.regionprops_table(
        label_image=nuclei_masks,
        intensity_image=cfos_img,
        properties=[
            "label",
            "intensity_mean",
            "intensity_max"
        ],
    )

    # Construct a dataframe
    cfos_df = pd.DataFrame(cfos_props)

    # Rename the intensity columns for further merging with cfos_df
    cfos_df.rename(columns={'intensity_mean': 'cfos_intensity_mean'}, inplace=True)
    cfos_df.rename(columns={'intensity_max': 'cfos_intensity_max'}, inplace=True)
    
    merged_df = pd.merge(cfos_df, h2a_df, on='label', how='inner')
    
    # Create a new DataFrame with the same index as merged_df and the new columns
    new_columns_df = pd.DataFrame({
        'filename': [filename] * len(merged_df),
        'region': [region] * len(merged_df),
        'mouse_id': [mouse_id] * len(merged_df),
        'ihc_round': [ihc_round] * len(merged_df)
    }, index=merged_df.index)

    # Concatenate the new columns DataFrame with the original merged_df
    # Using pd.concat and specifying axis=1 for columns, and placing the new DataFrame first
    merged_df = pd.concat([new_columns_df, merged_df], axis=1)
    
    dataframes.append(merged_df)


100%|██████████| 264/264 [18:58<00:00,  4.31s/it]


In [4]:
# Concatenate all DataFrames in the list into a single DataFrame
merged_df = pd.concat(dataframes, ignore_index=True)

In [5]:
merged_df.head()

filename region mouse_id ihc_round  label  cfos_intensity_mean  \
0   Image1    CA1   AD1867     IHC_1      1            13.225974   
1   Image1    CA1   AD1867     IHC_1      2            18.909594   
2   Image1    CA1   AD1867     IHC_1      3            19.713966   
3   Image1    CA1   AD1867     IHC_1      4            16.776413   
4   Image1    CA1   AD1867     IHC_1      5            18.487179   

   cfos_intensity_max  h2a_intensity_mean  h2a_intensity_max  area_filled  \
0                39.0           13.851299               58.0       1540.0   
1                38.0           21.547355               83.0       1626.0   
2                60.0            9.843778               62.0       2234.0   
3                40.0           13.968468               77.0       2442.0   
4                42.0           12.203360               59.0       1131.0   

    perimeter  equivalent_diameter  
0  154.568542            44.280796  
1  157.254834            45.500412  
2  180.367532            53.333077  
3  188.066017            55.760658  
4  127.053824            37.947779

In [6]:
merged_df.to_csv("results.csv")

In [7]:
import plotly.express as px

# Create a histogram of cfos_intensity_mean values
fig = px.histogram(merged_df, x='h2a_intensity_mean', nbins=50, title='Distribution of H2A Intensity Mean')

# Update layout if necessary
fig.update_layout(
    xaxis_title='H2A Intensity Mean',
    yaxis_title='Count',
    bargap=0.2
)

# Show the plot
fig.show()

In [8]:
import plotly.express as px

# Create a histogram of cfos_intensity_mean values
fig = px.histogram(merged_df, x='cfos_intensity_mean', nbins=50, title='Distribution of CFOS Intensity Mean')

# Update layout if necessary
fig.update_layout(
    xaxis_title='CFOS Intensity Mean',
    yaxis_title='Count',
    bargap=0.2
)

# Show the plot
fig.show()


In [9]:
import plotly.express as px

# Assuming 'df' is your DataFrame with the columns 'h2a_intensity_mean' and 'cfos_intensity_mean'
fig = px.scatter(merged_df, x='h2a_intensity_mean', y='cfos_intensity_mean', 
                 title='Correlation between H2A Intensity Mean and cFos Intensity Mean',
                 labels={'h2a_intensity_mean': 'H2A Intensity Mean', 'cfos_intensity_mean': 'cFos Intensity Mean'},
                 hover_data=[merged_df.index,'region', 'mouse_id', 'ihc_round', 'label'], # Shows the index, region, mouse_id... of the DataFrame on hover
                 trendline="ols")  

# Update layout if necessary
fig.update_layout(
    xaxis_title='H2A Intensity Mean',
    yaxis_title='cFos Intensity Mean'
)

# Show the plot
fig.show()


In [10]:
# Initialize napari.Viewer and display input stacks and label processing steps
# viewer = napari.Viewer(ndisplay=2)
# viewer.add_image(img)
# viewer.add_image(nuclei_img)
# viewer.add_image(post_gaussian_img)
# viewer.add_image(img_rescale)
# viewer.add_labels(nuclei_masks)